<div style="font-size: 50px; text-align: center" >Deadpool™️ Detector</div>



# Description
First development app using deep learning techniques. Stepping stone in my journey.

Given an image infer if it contains Deadpool in it.

# Train a model

## Training Data
Using [SH2022 Dataset](https://www.kaggle.com/datasets/muhammadhananasghar/sh2022-dataset) there is a labeled set of Deadpool images.

Add data to a `DataLoaders` object and display a batch

In [ ]:
from fastai.vision.all import *

data_path = Path('/home/zeus/data/SH2022')

dls = ImageDataLoaders.from_folder(
    path=data_path,
    train='train',
    valid='test/Deadpool',
    item_tfms=Resize(224),
    batch_tfms=aug_transforms()
)
dls.show_batch()

## Training

In [ ]:
learn = vision_learner(dls, resnet34, metrics=error_rate)
learn.fine_tune(3)

## Export Trained Model

In [ ]:
learn.export('/home/zeus/projects/Deadpool-Detector/deadpool-detection-model.pkl')

## Share Learner with the world!

In [5]:
from huggingface_hub import push_to_hub_fastai

learn = load_learner('/home/zeus/projects/Deadpool-Detector/deadpool-detection-model.pkl')
repo_id = "jeffreymjohnson/Deadpool-Detector"
push_to_hub_fastai(learner=learn, repo_id=repo_id)

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

model.pkl:   0%|          | 0.00/88.7M [00:00<?, ?B/s]

'https://huggingface.co/jeffreymjohnson/Deadpool-Detector/tree/main/'

# Create App

In [7]:
#|export
from huggingface_hub import from_pretrained_fastai

learner = from_pretrained_fastai("jeffreymjohnson/Deadpool-Detector")

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

In [8]:
#|export
labels = learn.dls.vocab
def predict(img):
    yes_reaction = "reactions/yes.jfif"
    no_reaction = "reactions/no.jfif"
    what_reaction = "reactions/what.jpg"
    
    img = PILImage.create(img)
    pred,pred_idx,probs = learn.predict(img)
    index = pred_idx.item()
    probability = probs[index].item()
    isDeadpool = pred == "Deadpool"
    
    if isDeadpool:
        x = "is"
    else:
        x = "is not"
    
    #print("The probability is: [" + str(probability) + "] that this " + x + " Deadpool")
    
    if probability < .75:
        return PILImage.create(what_reaction)
    elif isDeadpool:
        return PILImage.create(yes_reaction)
    else:
        return PILImage.create(no_reaction)

In [9]:
#|export
import gradio as gr

demo = gr.Interface(
    title="Deadpool™️ Detector",
    fn=predict,
    inputs=gr.Image(shape=(200,200)),
    outputs=gr.Image(shape=(200,200)), 
    examples=["examples/deadpool_example1.jpg", "examples/deadpool_example2.jpg", "examples/deadpool_example3.jpg", "examples/spiderman.jpg",]
).launch(share=true)

Running on local URL:  http://127.0.0.1:7860
Running on public URL: https://ed025bd9d3a5e5798f.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades (NEW!), check out Spaces: https://huggingface.co/spaces


The probability is: [0.9999980926513672] that this is Deadpool


The probability is: [0.9999998807907104] that this is not Deadpool
